In [1]:
from math import sqrt
import matplotlib.pyplot as plt
import numpy as np
from GPy.models import GPRegression
import GPy
from emukit.model_wrappers import GPyModelWrapper
from emukit.experimental_design.acquisitions import IntegratedVarianceReduction
from emukit.core import ContinuousParameter, ParameterSpace
from emukit.core.acquisition.acquisition_per_cost import acquisition_per_expected_cost
from emukit.core.interfaces.models import IModel
from emukit.experimental_design import ExperimentalDesignLoop
import plotly.graph_objects as go
import itertools
from sklearn.svm import SVR
import copy
from mfed.pde import pde_runner
from mfed.plot import plot
from IPython.display import Video


## Define PDE and parameters

Parmaters of interest:
- pde_name: Describe the PDE equations used
- t_range: how much time do we run the simulation forward in time 
- diff: Diffusivity coefficient
- seed: random seed used for reproducibility
- dim_data: dimension of the parameter space (usually 1 in this notebook)
- f_y: function that we use to derive the Y values. In this case it counts how many values are above 4.25

In [2]:
f_y = lambda x: len(np.where(x > 4.25)[0])

param = {"pde_name":"brusselator","t_range":10,"diff":1,"dt":1e-03,"seed":100,"dim_data":1,"f_y":f_y}

pde_client = pde_runner(param,f_y)
Video("./../assets/brusselator/baseline.mp4")

## Create initial data

We use this inital data to fit the first GP. The boundary of the sampled data also represents the boundary of the experimental design loop. 

In [3]:
# Cost is rougly 100x between -1 and -3
dt_list = [1e-01,1e-03] # 
diff_list = np.linspace(0.1,0.9,2)
X = np.array(list(itertools.product(dt_list,diff_list)))
Y = pde_client(X)


100%|██████████| 4/4 [01:25<00:00, 21.36s/it]


In [4]:
# Boiler plate for plotting 
mesh_size = 50
space = ParameterSpace([ContinuousParameter('diff', X[:,0].min(), X[:,0].max()),
                        ContinuousParameter('dt', X[:,1].min(), X[:,1].max())])
x_monte_carlo = np.vstack([np.ones((mesh_size))*space.parameters[0].min,
                np.linspace(X[:,1].min(),X[:,1].max(),mesh_size)]).T



In [5]:
# Define and fit a GP model 

kernel = GPy.kern.RBF(input_dim=2,ARD=True,lengthscale=[1,1],variance=1)
model_gpy = GPRegression(X,Y,kernel = kernel,normalizer=True,noise_var=0.05)
model_gpy.parameters[0].variance.fix()
model_gpy.parameters[1].variance.fix()



Param:  [1.   1.   1.   0.05]


In [6]:

model_emukit = GPyModelWrapper(model_gpy)
model_variance = IntegratedVarianceReduction(model=model_emukit,space=space,x_monte_carlo=x_monte_carlo)
plot(X,Y,model_variance)




In [7]:
class CostModel(IModel):
    def __init__(self,pde_client):
        self.clf = SVR()
        self.pde_client = pde_client
        self.fit()
    
    def fit(self):
        dt = np.array(self.pde_client.cost)[:,0].reshape((-1,1))
        cost = np.array(self.pde_client.cost)[:,1]
        self.clf.fit(dt,cost)

    def predict(self, X: np.ndarray):
        w = self.clf.predict(X[:,0].reshape((-1,1))).reshape((-1,1))
        return (w,X)


cost_model = CostModel(pde_client) # Fit a linear model on the costs 
weighted_variance = acquisition_per_expected_cost(model_variance,cost_model)
plot(X,Y,weighted_variance)

In [8]:

model_emukit = GPyModelWrapper(model_gpy)

expdesign_loop = ExperimentalDesignLoop(model = model_emukit,
                                        space = space,
                                        acquisition = weighted_variance,
                                        batch_size = 1)

In [9]:
max_iterations = 10
for i in range(max_iterations):
    expdesign_loop.run_loop(pde_client, 1)
    cost_model.fit()
    X_new = np.array([i.X for i in expdesign_loop.loop_state.results])
    Y_new = np.array([i.Y for i in expdesign_loop.loop_state.results])
    model_variance = IntegratedVarianceReduction(model=expdesign_loop.model,space=space,x_monte_carlo=x_monte_carlo)
    weighted_variance = acquisition_per_expected_cost(model_variance,cost_model)
    plot(np.vstack((X,X_new)),np.vstack((Y,Y_new)),weighted_variance)


    

100%|██████████| 1/1 [00:19<00:00, 19.17s/it]


100%|██████████| 1/1 [00:20<00:00, 20.39s/it]


100%|██████████| 1/1 [00:21<00:00, 21.12s/it]


100%|██████████| 1/1 [00:18<00:00, 18.66s/it]


100%|██████████| 1/1 [00:18<00:00, 18.89s/it]


100%|██████████| 1/1 [00:26<00:00, 26.05s/it]


100%|██████████| 1/1 [00:20<00:00, 20.31s/it]


100%|██████████| 1/1 [00:18<00:00, 18.86s/it]


100%|██████████| 1/1 [00:19<00:00, 19.13s/it]


100%|██████████| 1/1 [00:29<00:00, 29.60s/it]


### Follow up

- You can play around and create scenarios where the lower resolution are not useful (by changing the range of dt for example). 
- Some PDE are smoother than other. You can use the diffusion equation which is very smooth.
- You can also modify the f_y function.

### Some issue

- Greedy behavior is suboptimal
